In [36]:
from functions_collection_copy import *
import random as random
import statistics
import csv

def new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='0', check_integrity=False):
    # Make a matrix to hold pairwise alignment costs for all alignment combinations!
    matrix = np.full((len(seqs), len(seqs)), np.nan)
    # Loop over all pairs
    for i, seq1 in enumerate(seqs):
        for j, seq2 in enumerate(seqs):
            matrix[i, j] = get_cost_2(linear_C(gap_cost, score_matrix, seq1, seq2))
    matrix_for_MST=matrix #copy the matrix, so that we ca keep the old matrix and make a changed version to the "pseudomatrix" version
    matrix_for_MST=convert_to_desired_format_nr_version(matrix_for_MST) #making the "pseudomatrix"
    if starting_node=='mid':
        starting_node=str(np.argmin(matrix.sum(axis=1)))
    elif starting_node=='ex':
        starting_node=str(np.argmax(matrix.sum(axis=1)))
    elif starting_node=='rd':
        starting_node=str(np.random.randint(0,matrix.shape[0]))
    elif starting_node=="min_sn":
        starting_node=str(np.unravel_index(np.argmin(matrix), matrix.shape)[0])
    elif starting_node=="max_sn":
        starting_node=str(np.unravel_index(np.argmax(matrix), matrix.shape)[0])
    else:
        starting_node='0'
    min_span_edges_res=find_min_span_edges_Prim(matrix_for_MST, starting_node)
    in_which_MSA_is_it={}
    names=set()
    for element in min_span_edges_res:
        print(element[2], element[3])
        names.add(element[2])
        names.add(element[3])
    in_which_MSA_is_it ={name: [int(name),0] for name in names}
    MSA_list=[[[char] for char in seq] for seq in seqs]
    who_aligned_to_who=[]
    for row in min_span_edges_res:
        node1=row[2]
        node2=row[3]
        who_aligned_to_who.append([node1,node2])
    for element in min_span_edges_res:
            node1=element[2]
            node2=element[3]
            cost=linear_C(gap_cost,score_matrix,seqs[int(node1)],seqs[int(node2)])
            alignment1_str,alignment2_str=linear_backtrack(seqs[int(node1)], seqs[int(node2)], cost, score_matrix, gap_cost)
            alignment1, alignment2 = [*alignment1_str], [*alignment2_str]
            A = [list(e) for e in zip(alignment1,alignment2)]
            united_MSA_new=alt_alt_merge_united(A,MSA_list,in_which_MSA_is_it,node1,node2)
            in_which_MSA_is_it, MSA_list=perform_updates_OBO(in_which_MSA_is_it, node1, node2, united_MSA_new, MSA_list)
    total_cost = compute_cost(MSA_list[0], score_matrix, gap_cost)
    if check_integrity==True:
       integrity_check_OBO_and_gradual(seqs,in_which_MSA_is_it,who_aligned_to_who,MSA_list, matrix,score_matrix,gap_cost)
    total_cost = compute_cost(MSA_list[0], score_matrix, gap_cost)
    return(matrix,MSA_list, total_cost)



In [52]:
score_matrix={'a': {'a': 0, 'c': 5, 'g': 2, 't': 5}, 'c': {'a': 5, 'c': 0, 'g': 5, 't': 2}, 'g': {'a': 2, 'c': 5, 'g': 0, 't': 5}, 't': {'a': 5, 'c': 2, 'g': 5, 't': 0}}
gap_cost=5
seqs=['aaatt',
 'cagtcgtt',
 'agctg',
 'ctgtagaac',
 'gcagg',
 'tttttt',
 'agcggcg',
 'cacccgtga',
 'tctgcag',
 'taactcata']

zero=new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='0', check_integrity=False)[2]

mid=new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='mid', check_integrity=False)[2]

ex=new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='ex', check_integrity=False)[2]

rd=new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='rd', check_integrity=False)[2]

min_sn=new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='min_sn', check_integrity=False)[2]

max_sn=new_assembly_Prim_starting_node_diff(seqs,score_matrix,gap_cost,starting_node='max_sn', check_integrity=False)[2]

print(zero,mid,ex,rd, min_sn,max_sn)



0 2
2 6
4 6
0 1
1 9
7 9
4 8
1 5
1 3
<class 'dict'>
{'7': [7, 0], '4': [4, 0], '1': [1, 0], '9': [9, 0], '5': [5, 0], '0': [0, 0], '2': [2, 0], '8': [8, 0], '6': [6, 0], '3': [3, 0]}
<class 'numpy.str_'>
<class 'numpy.str_'>
the node1 is right now in the alignment nr 0
the node2 is right now in the alignment nr 2
I don't have the case identified yet, but MSA1 is: ['a'] MSA2 is: ['a'] ,and the guide is: ['a', 'a']
nodes pointing to cols: 0 , 0
i,j,l: 0,0,0
max for those should be: 5,5,5
flag: False
case:3
guide_was: ['a', 'a']
I just made the new col: ['a', 'a']
MSA_new now has len: 1
['a', 'a']
selected stuff from col made: 
['a', 'a']
I don't have the case identified yet, but MSA1 is: ['a'] MSA2 is: ['g'] ,and the guide is: ['a', 'g']
nodes pointing to cols: 0 , 0
i,j,l: 1,1,1
max for those should be: 5,5,5
flag: False
case:3
guide_was: ['a', 'g']
I just made the new col: ['a', 'g']
MSA_new now has len: 2
['a', 'g']
selected stuff from col made: 
['a', 'g']
I don't have the case identi

In [38]:
csv_file_path="cost_different_starting_nodes_prim_15reps_10str.csv"
with open(csv_file_path, 'a', newline='') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow('str_len,zero,mid,ex,rd,min_sn,max_sn')

str_lens=[5,10,20,50]
for nr in str_lens:
    zero_cost=[]
    mid_cost=[]
    ex_cost=[]
    rd_cost=[]
    min_sn_cost=[]
    max_sn_cost=[]
    repeats=15
    nr_of_str=10
    len_str=nr
    random_sequences_collection=[]
    for i in range(0,repeats):
        random_pile=[]
        for j in range (0,nr_of_str):
            a_sequence=[]
            for k in range(0,len_str):
                a_sequence.append(random.choice(['a','c','t','g']))
            a_sequence=''.join(a_sequence)
            random_pile.append(a_sequence)
        random_sequences_collection.append(random_pile)  
    for random_pile in random_sequences_collection:
        zero=new_assembly_Prim_starting_node_diff(random_pile,score_matrix,gap_cost,starting_node='0', check_integrity=False)[2]
        zero_cost.append(zero)

        mid=new_assembly_Prim_starting_node_diff(random_pile,score_matrix,gap_cost,starting_node='mid', check_integrity=False)[2]
        mid_cost.append(mid)

        ex=new_assembly_Prim_starting_node_diff(random_pile,score_matrix,gap_cost,starting_node='ex', check_integrity=False)[2]
        ex_cost.append(ex)

        rd=new_assembly_Prim_starting_node_diff(random_pile,score_matrix,gap_cost,starting_node='rd', check_integrity=False)[2]
        rd_cost.append(rd)
        
        min_sn=new_assembly_Prim_starting_node_diff(random_pile,score_matrix,gap_cost,starting_node='min_sn', check_integrity=False)[2]
        min_sn_cost.append(min_sn)

        max_sn=new_assembly_Prim_starting_node_diff(random_pile,score_matrix,gap_cost,starting_node='max_sn', check_integrity=False)[2]
        max_sn_cost.append(max_sn)

    print("Mean cost str len ", str(nr)," zero:")
    print(statistics.mean(zero_cost))
    print("Mean cost str len ", str(nr),"mid:")
    print(statistics.mean(mid_cost))
    print("Mean cost str len ", str(nr)," ex:")
    print(statistics.mean(ex_cost))
    print("Mean cost str len ", str(nr)," rd:")
    print(statistics.mean(rd_cost))
    print("Mean cost str len ", str(nr)," min_sn:")
    print(statistics.mean(min_sn_cost))
    print("Mean cost str len ", str(nr)," max_sn:")
    print(statistics.mean(max_sn_cost))


    with open(csv_file_path, 'a', newline='') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow([nr,round(statistics.mean(zero_cost),2),round(statistics.mean(mid_cost),2),round(statistics.mean(ex_cost),2),round(statistics.mean(rd_cost),2),round(statistics.mean(min_sn_cost),2),round(statistics.mean(max_sn_cost),2)])
        

0 2
2 4
4 8
2 3
3 7
1 3
3 9
6 7
5 8
<class 'dict'>
{'7': [7, 0], '4': [4, 0], '1': [1, 0], '9': [9, 0], '5': [5, 0], '0': [0, 0], '2': [2, 0], '8': [8, 0], '6': [6, 0], '3': [3, 0]}
<class 'numpy.str_'>
<class 'numpy.str_'>
the node1 is right now in the alignment nr 0
the node2 is right now in the alignment nr 2
I don't have the case identified yet, but MSA1 is: ['t'] MSA2 is: ['c'] ,and the guide is: ['t', 'c']
nodes pointing to cols: 0 , 0
i,j,l: 0,0,0
max for those should be: 5,5,5
flag: False
case:3
guide_was: ['t', 'c']
I just made the new col: ['t', 'c']
MSA_new now has len: 1
['t', 'c']
selected stuff from col made: 
['t', 'c']
I don't have the case identified yet, but MSA1 is: ['t'] MSA2 is: ['g'] ,and the guide is: ['t', 'g']
nodes pointing to cols: 0 , 0
i,j,l: 1,1,1
max for those should be: 5,5,5
flag: False
case:3
guide_was: ['t', 'g']
I just made the new col: ['t', 'g']
MSA_new now has len: 2
['t', 'g']
selected stuff from col made: 
['t', 'g']
I don't have the case identi

KeyboardInterrupt: 

In [45]:
# Create a NumPy matrix (replace this with your matrix)
matrix = np.array([[3, 5, 2],
                   [8, 1, 7],
                   [4, 6, 9]])

# Find the indices of the minimum value
min_index = np.unravel_index(np.argmax(matrix), matrix.shape)[0]

min_index

2